In [1]:
import os
from dotenv import load_dotenv

load_dotenv()

True

In [2]:
import sys

IMPL_PATH = os.getenv("IMPL_PATH")
sys.path.append(IMPL_PATH)
DATA_PATH = IMPL_PATH + "/data/"
print(DATA_PATH)

/home/hoangbaoan1901/Documents/information-system_UET/sem5/ai/BTL/INT3401-Midterm/implementations/data/


### HYPER-PARAM

In [3]:
TIME_STEP = 6
FUTURE_STEP = 1
N_CLUSTERS = 4

### Training configs:
1. XGB classifier, Random Forest Classifier
2. Random Forest regression, MLP regression

### Load data from pickle files (made from 1_group_data.ipynb)

In [4]:
import pickle
import pandas as pd
import numpy as np

train_4_clusters = pickle.load(open(DATA_PATH + "train_4_clusters.pkl", "rb"))
test_4_clusters = pickle.load(open(DATA_PATH + "test_4_clusters.pkl", "rb"))
train_10_clusters = pickle.load(open(DATA_PATH + "train_10_clusters.pkl", "rb"))
test_10_clusters = pickle.load(open(DATA_PATH + "test_10_clusters.pkl", "rb"))

In [5]:
# More insights
print(type(train_4_clusters))
print(type(train_4_clusters[0]))
print(type(train_4_clusters[0][list(train_4_clusters[0].keys())[0]]))
train_4_clusters[0][list(train_4_clusters[0].keys())[0]].head()

<class 'list'>
<class 'dict'>
<class 'pandas.core.frame.DataFrame'>


date  aws    imerge      tclw     cape       r850       tcwv  \
0 2019-04-05 00:00:00  0.0  0.000000  0.601746  764.875  101.99864  40.422440   
1 2019-04-05 01:00:00  0.0  2.344666  0.718018  718.250  101.55731  40.268112   
2 2019-04-05 02:00:00  0.0  0.000000  0.726501  641.500  100.97389  40.492720   
3 2019-04-05 03:00:00  0.0  0.000000  0.802307  657.750  101.41234  41.193832   
4 2019-04-05 04:00:00  0.0  0.000000  0.789673  768.375  101.11197  41.474990   

         tcw      isor       cin  ...       b14b       b12b        wvb  \
0  41.102127  0.639833  1.234695  ...  284.33180  261.34055  241.05534   
1  41.090378  0.639833  1.609385  ...  269.04214  253.95319  233.24005   
2  41.336470  0.639833  4.781275  ...  265.27927  251.04973  230.30144   
3  42.069046  0.639833  0.922052  ...  250.11890  241.74947  227.51172   
4  42.352478  0.639833  1.031371  ...  269.80673  252.86195  231.27336   

        b10b        i4b       b11b        i2b       b09b       b16b        irb  
0  262.45953  287.18150  281.60117  282.42870  254.15454  269.72195  284.27634  
1  252.26457  285.38474  269.76950  266.40400  244.32185  255.54140  270.90137  
2  248.32812  288.52264  265.98843  262.90793  239.77428  253.72685  266.85617  
3  239.57889  274.33460  251.26399  248.57503  234.14128  242.58984  251.76514  
4  250.37960  293.51816  269.01328  267.80804  241.04387  257.99274  270.40110  

[5 rows x 22 columns]

### For each month, for each cluster, convert the dictionary into corresponding X and y

In [ ]:
import data_processors as dp
ts_processor = dp.TimeSeriesProcessor(time_step=TIME_STEP, future_step=FUTURE_STEP)
train_4_clustered_list = []
test_4_clustered_list = []
train_10_clustered_list = []
test_10_clustered_list = []

for cluster in range(N_CLUSTERS):
	train_4_clustered_list.append(ts_processor.get_sequence_data_for_cluster(train_4_clusters[cluster]))
	test_4_clustered_list.append(ts_processor.get_sequence_data_for_cluster(test_4_clusters[cluster]))
	train_10_clustered_list.append(ts_processor.get_sequence_data_for_cluster(train_10_clusters[cluster]))
	test_10_clustered_list.append(ts_processor.get_sequence_data_for_cluster(test_10_clusters[cluster]))

df.shape: (1032, 22)
find_continuous: len(continuous_dfs): 58
create_sequence_data: X shape: (48, 6, 21), y shape: (48,)
create_sequence_data: X shape: (17, 6, 21), y shape: (17,)
create_sequence_data: X shape: (15, 6, 21), y shape: (15,)
create_sequence_data: X shape: (14, 6, 21), y shape: (14,)
create_sequence_data: X shape: (7, 6, 21), y shape: (7,)
time_step + future_step - 1 = 6 must be less than the length of the DataFrame(1)
time_step + future_step - 1 = 6 must be less than the length of the DataFrame(3)
create_sequence_data: X shape: (14, 6, 21), y shape: (14,)
create_sequence_data: X shape: (15, 6, 21), y shape: (15,)
create_sequence_data: X shape: (14, 6, 21), y shape: (14,)
create_sequence_data: X shape: (15, 6, 21), y shape: (15,)
create_sequence_data: X shape: (18, 6, 21), y shape: (18,)
create_sequence_data: X shape: (40, 6, 21), y shape: (40,)
create_sequence_data: X shape: (9, 6, 21), y shape: (9,)
time_step + future_step - 1 = 6 must be less than the length of the Data

In [7]:
# test for april training data
print(len(train_4_clustered_list)) # 4 Cluster
train_4_cluster_0 = train_4_clustered_list[0] # lots of train data
X, y = train_4_cluster_0
print(X.shape)
print(y.shape)

# Count number of nan values
print(np.sum(np.isnan(X)))
print(np.sum(np.isnan(y)))

# Count number of 0 values
print(np.sum(X == 0))
print(np.sum(y == 0))

4
(23210, 6, 21)
(23210,)
0
0
261524
21581


### Normalize X features

In [ ]:
for i in range(N_CLUSTERS):
    X_train_4, 